# **1. Corpus**

## Crawl URLs to extract all internal links 

**XENU Link Sleuth**  
https://home.snafu.de/tilman/xenulink.html 

*Le logiciel XENU Link Sleuth a finalement été retenu pour cette tâche* 

## Scrape textual data from crawled URLs
**BeautifulSoup HTML Parser**  
Réf : https://realpython.com/python-web-scraping-practical-introduction/

In [47]:
path = 'D:/1-XENU_crawl/csv_html_pdfs/'
acteur = "chuqc"

La liste des URLs à scrapper pour chaque corpus est contenue dans un fichier CSV. 
On commence donc par lire le CSV pour extraire nos URLS.

In [48]:
from pandas import *

# encoding= 'ISO-8859-1' "utf-8"
path = 'D:/1-XENU_crawl/csv_html_pdfs/'
with open(path + acteur + '.csv', encoding='utf-8') as f:
    csv = read_csv(f, sep=';')

csv

Address             Type  \
0               https://www.chudequebec.ca/accueil.aspx        text/html   
1     https://www.chudequebec.ca/patient/maladies-so...        text/html   
2     https://www.chudequebec.ca/visiteur/connaitre-...        text/html   
3     https://www.chudequebec.ca/a-propos-de-nous/qu...        text/html   
4     https://www.chudequebec.ca/a-propos-de-nous/qu...        text/html   
...                                                 ...              ...   
1141  https://www.chudequebec.ca/a-propos-de-nous/pu...        text/html   
1142  https://www.chudequebec.ca/getmedia/0c40571f-2...  application/pdf   
1143  https://www.chudequebec.ca/CMSPages/Dialogs/Ca...        text/html   
1144  https://www.chudequebec.ca/getattachment/8b5eb...              NaN   
1145  https://www.chudequebec.ca/getattachment/b0f23...              NaN   

                                                  Title Charset  \
0     Accueil | CHU de Qu&#233;bec-Universit&#233; L...   utf-8   
1     Centre int&#233;gr&#233; de canc&#233;rologie ...   utf-8   
2     Heures de visites | CHU de Qu&#233;bec-Univers...   utf-8   
3     Qui sommes-nous? | CHU de Qu&#233;bec-Universi...   utf-8   
4     Code d&#39;&#233;thique | CHU de Qu&#233;bec-U...   utf-8   
...                                                 ...     ...   
1141             L&#39;EXP&#201;RIENCE DE LA SOUFFRANCE   utf-8   
1142                            tMedia_sSsante_2022.pdf   utf-8   
1143                                      Security code   utf-8   
1144                                                NaN   utf-8   
1145                                                NaN   utf-8   

                                            Description  
0     Page d&#39;accueil du site Internet du CHU de ...  
1     Centre int&#233;gr&#233; de canc&#233;rologie ...  
2     Heures de visites pour les proches aidants acc...  
3     Description du CHU de Qu&#233;bec-Universit&#2...  
4     Le nouveau Code d&#39;&#233;thique du CHU de Q...  
...                                                 ...  
1141                                                NaN  
1142                                                NaN  
1143                                                NaN  
1144                                                NaN  
1145                                                NaN  

[1146 rows x 5 columns]

In [49]:
#liste = csv[csv['Type'] != 'application/pdf'] # On va scraper les PDFs avec une autre librairie que BeautifulSoup

liste = csv['Address'].tolist()
liste = [lien for lien in liste if not lien.endswith('pdf')]

In [50]:
import requests, re, ssl, os, sys, pandas as pd
from bs4 import BeautifulSoup
#from requests.packages.urllib3.util.retry import Retry

def getTextURL(url):    
    html = requests.get(url, headers = {'User-Agent': 'My User Agent 1.0'}, verify=False)
    html.encoding = 'utf-8'
    html = html.text
   
    soup = BeautifulSoup(html, "html.parser")
    data = soup.get_text(separator=' ').replace("\n", " ").replace("\r", " ").replace(u'\xa0', u' ')
    data = re.compile(r"\s+").sub(" ", data).strip() + "\n\n"
    
    return data

In [51]:
output = []

erreur = 0
for site in liste: 
    try: 
        text = getTextURL(site)
        output.append({'url': site, 'text':text})
        
    except Exception as e:
        print("ERROR " + " - " + site)
        print(e)
        erreur +=1 

c:\Users\p1115145\AppData\Local\Programs\Python\Python310\lib\site-packages\urllib3\connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.chudequebec.ca'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
c:\Users\p1115145\AppData\Local\Programs\Python\Python310\lib\site-packages\urllib3\connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.chudequebec.ca'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
c:\Users\p1115145\AppData\Local\Programs\Python\Python310\lib\site-packages\urllib3\connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.chudequebec.ca'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/

In [ ]:
output

[{'url': 'https://pinel.qc.ca/',
  'text': "Accueil - Institut national de psychiatrie légale Philippe-Pinel A A A Événements Nouvelles COVID-19 Carrières Forensia Fondation Soins aux patients Familles et visiteurs Services aux professionnels Recherche Volet académique L’Institut Menu Soins aux patients Voir tout Philosophie des soins Expertise, sécurité des soins, équipes, éthique, intégration sociale Programmes et traitements Programmes et traitements offerts aux patients internes Aide et ressources Aide et ressources disponibles pour les patients et leurs proches Activités des patients Activités créatives, physiques et intellectuelles pour les patients Les installations Milieu de vie, unités de soins, visite virtuelle Approche interdisciplinaire Accompagner la personne dans son rétablissement Commissaire local aux plaintes et à la qualité des services Commissaire local aux plaintes et procédures pour porter plainte Programme québécois pour les troubles mentaux Des autosoins à la psy

In [ ]:
df = pd.DataFrame(output)
output_path = 'D:/1-XENU_crawl/csv_html_pdfs/'

df.to_csv(output_path + acteur + '_DATA.csv', escapechar='/')

In [ ]:
print('Au total, il y a {} pages'.format(erreur) + ' qui n\'ont pas pu être aspirées sur les {} URLs de notre liste'.format(len(liste)))

Au total, il y a 0 pages qui n'ont pas pu être aspirées sur les 523 URLs de notre liste
